# Load Data

In [28]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd

from sklearn.model_selection import train_test_split

from sklearn.preprocessing import StandardScaler
from sklearn.linear_model import LinearRegression
from sklearn.feature_selection import SelectFromModel

import pickle

import gc
import os
working_directory = 'D:\\OneDrive - 한동대학교\\PROJECT\\트머프로젝트\\'  ## 서로 다른 환경에서는 이곳을 수정해야 함.
# working_directory = 'C:\\Users\\user\\OneDrive - 한동대학교\\PROJECT\\트머프로젝트\\'

os.chdir(working_directory)
gc.collect()

# load dataset
coin = 'BTC'
target_var = 'dv5_realized_volatility_mean0'
target_var_3 = target_var[:3]

# data = pd.read_csv("./output/{}_sum_plus_nn_features_for_{}.csv".format(coin, target_var_3))
data = pd.read_csv("./output/temp_1105_first_30000.csv")

# In practice, feature selection should be done after data pre-processing,
# so ideally, all the categorical variables are encoded into numbers,
# and then you can assess how deterministic they are of the target

# here for simplicity I will use only numerical variables
# select numerical columns:

numerics = ['int16', 'int32', 'int64', 'float16', 'float32', 'float64']
numerical_vars = list(data.select_dtypes(include=numerics).columns)
data = data[numerical_vars]

In [29]:
print(data.shape) # Check the shape of NN file.

pd.set_option('display.max_columns', None)
data.head(3) 

# five features are dep.
# so, # of features after adding NN features is 18,237.

(8411, 9050)


realized_volatility_mean0  num_trades  lowest_return  highest_return  \
0                   0.000155         338      -0.001160        0.000186   
1                   0.000177         359      -0.000789        0.000557   
2                   0.000178         363      -0.000789        0.000557   

   high_low_gap  trade_vol  BB_width_w20  BB_width_w40  BB_width_w10  \
0      0.001346  12.049068     20620.889     27210.670     22881.336   
1      0.001346  13.103086     19948.354     23676.451     23232.162   
2      0.001346  12.706044     19095.328     20188.852     22799.610   

   dv5_realized_volatility_mean0  dv2_lowest_return  dv3_highest_return  \
0                       0.000191          -0.001207            0.000232   
1                       0.000160          -0.001207            0.000000   
2                       0.000159          -0.001114            0.000139   

   realized_volatility_mean0_150  num_trades_150  lowest_return_150  \
0                       0.000114              44          -0.000464   
1                       0.000045              54          -0.000186   
2                       0.000042              57          -0.000232   

   highest_return_150  high_low_gap_150  trade_vol_150  \
0            0.000000          0.000464       1.894086   
1            0.000046          0.000232       2.382331   
2            0.000000          0.000232       2.608287   

   realized_volatility_mean0_300  num_trades_300  lowest_return_300  \
0                       0.000077             119          -0.000603   
1                       0.000075             143          -0.000325   
2                       0.000188             195          -0.000789   

   highest_return_300  high_low_gap_300  trade_vol_300  \
0            0.000000          0.000603       4.710686   
1            0.000232          0.000557       6.082892   
2            0.000371          0.001160       8.167232   

   realized_volatility_mean0_450  num_trades_450  lowest_return_450  \
0                       0.000174             248          -0.001160   
1                       0.000161             277          -0.000789   
2                       0.000157             296          -0.000789   

   highest_return_450  high_low_gap_450  trade_vol_450  liq_last_1  \
0            0.000186          0.001346       9.954347    0.000105   
1            0.000557          0.001346      10.510321    0.000224   
2            0.000557          0.001346      10.489419    0.000375   

   liq_last_2  liq_last_5  liq_last_10  liq_last_15  ep_liq_1  ep_liq_2  \
0    0.000217    0.000476     0.000696     0.000837  0.000424  0.000537   
1    0.000399    0.000656     0.000909     0.001050  0.000350  0.000463   
2    0.000808    0.001140     0.001438     0.001531  0.000346  0.000469   

   ep_liq_5  ep_liq_10  ep_liq_15  bidask_spread_0  bidask_spread_1  \
0  0.000810   0.001057   0.001180         7.366460        13.832298   
1  0.000722   0.000962   0.001094        11.097345        24.778760   
2  0.000731   0.000968   0.001098         3.895833        13.635417   

   liq_last_1_150  liq_last_2_150  liq_last_5_150  liq_last_10_150  \
0        0.001113        0.001132        0.001422         0.001878   
1        0.001081        0.001097        0.001279         0.001598   
2        0.000346        0.000871        0.001061         0.001390   

   liq_last_15_150  ep_liq_1_150  ep_liq_2_150  ep_liq_5_150  ep_liq_10_150  \
0         0.002048      0.000524      0.000674      0.000999       0.001334   
1         0.001868      0.000588      0.000739      0.001014       0.001419   
2         0.001598      0.000529      0.000768      0.001011       0.001411   

   ep_liq_15_150  bidask_spread_0_150  bidask_spread_1_150  liq_last_1_300  \
0       0.001504             2.000000             5.318182        0.000140   
1       0.001632             1.142857             3.964286        0.000055   
2       0.001658             1.529412             4.529412        0.000078   

   liq_last_2

# Remove Row Data to Selection

In [30]:
print("Before remove target_var's threshold : " , data.shape)

# 'dv1_realized_volatility' 열의 25%와 75% 백분위수 계산 => dv5
percentile_10 = data[target_var].quantile(0.10)
percentile_90 = data[target_var].quantile(0.90)

# 0~25%와 75~100% 범위 밖의 행 제거
data_q1q4 = data[(data[target_var] <= percentile_10) | (data[target_var] >= percentile_90)]

print("After remove target var's threshold : " , data_q1q4.shape)

Before remove target_var's threshold :  (8411, 9050)
After remove target var's threshold :  (1684, 9050)


In [31]:
y = data_q1q4[target_var]
# drop_list = [] # 'dv1_realized_volatility','dv2_lowest_return','dv3_highest_return','dv4_realized_volatility_30s','dv5_realized_volatility_mean0'
# drop_list.append(target_var)
X = data_q1q4 # .drop(drop_list, axis=1)
# X = data_q1q4.drop(['realized_volatility', 'realized_volatility_150', 'realized_volatility_300', 'realized_volatility_450'], axis=1)
# print(X.shape)

# Feature Selection (0)
## Remove Corrlative Features

In [32]:
from scipy.stats import kendalltau

correlation_matrix = X.corr(method=lambda x, y: kendalltau(x, y).correlation)
correlation_matrix_series = correlation_matrix[target_var].copy() # .sort_values(ascending=False)
correlation_matrix_series.sort_values(ascending=False, inplace=True)
correlation_matrix_series

dv5_realized_volatility_mean0                                               1.000000
dv5_realized_volatility_mean0_nn16_all_nn_m_p1_mean                         0.577349
dv5_realized_volatility_mean0_nn8_all_nn_m_p1_mean                          0.571139
dv5_realized_volatility_mean0_nn1_all_nn_m_p1_median                        0.562202
dv5_realized_volatility_mean0_nn1_all_nn_m_p1_mean                          0.562202
dv5_realized_volatility_mean0_nn4_all_nn_m_p1_mean                          0.561237
dv5_realized_volatility_mean0_nn2_all_nn_m_p1_mean                          0.549803
dv5_realized_volatility_mean0_nn2_all_nn_m_p1_median                        0.549803
dv5_realized_volatility_mean0_nn16_all_nn_m_p1_median                       0.542546
dv5_realized_volatility_mean0_nn4_all_nn_m_p1_median                        0.537301
dv5_realized_volatility_mean0_nn16_high5_nn_m_mean                          0.533521
dv5_realized_volatility_mean0_nn8_all_nn_m_p1_median             

In [34]:
pd.set_option('display.max_rows', None)

print (correlation_matrix_series)

dv5_realized_volatility_mean0                                               1.000000
dv5_realized_volatility_mean0_nn16_all_nn_m_p1_mean                         0.577349
dv5_realized_volatility_mean0_nn8_all_nn_m_p1_mean                          0.571139
dv5_realized_volatility_mean0_nn1_all_nn_m_p1_median                        0.562202
dv5_realized_volatility_mean0_nn1_all_nn_m_p1_mean                          0.562202
dv5_realized_volatility_mean0_nn4_all_nn_m_p1_mean                          0.561237
dv5_realized_volatility_mean0_nn2_all_nn_m_p1_mean                          0.549803
dv5_realized_volatility_mean0_nn2_all_nn_m_p1_median                        0.549803
dv5_realized_volatility_mean0_nn16_all_nn_m_p1_median                       0.542546
dv5_realized_volatility_mean0_nn4_all_nn_m_p1_median                        0.537301
dv5_realized_volatility_mean0_nn16_high5_nn_m_mean                          0.533521
dv5_realized_volatility_mean0_nn8_all_nn_m_p1_median             

In [35]:
def correlation(dataset, threshold, target_var):
    col_corr = set()  # Set of all the names of correlated columns
    corr_matrix = dataset.corr()
    
    print("correlation calculation, done") 

    for i in range(len(corr_matrix.columns)):
        if i % 10 == 0:
            print("progress:", "{:.2f}".format((i/len(corr_matrix.columns)*100)), "%")        
        for j in range(i) :
            if (abs(corr_matrix.iloc[i, j]) > threshold) & (abs(corr_matrix.iloc[i, j]) < 1): # we are interested in absolute coeff value
                
                # Drop one of them with lower correlation with our target variable.
                if corr_matrix[target_var][i] >= corr_matrix[target_var][j]:
                    colname = corr_matrix.columns[j]  # getting the name of column
                elif corr_matrix[target_var][i] < corr_matrix[target_var][j]:
                    colname = corr_matrix.columns[i]  # getting the name of column        
                col_corr.add(colname)
                
    return col_corr

# note that we reduce the correlation threshold
# to remove more features
corr_cutpoint = 90
corr_features = correlation(X.sample(n=1000, random_state=42), corr_cutpoint/100, target_var)
print('correlated features: ', len(set(corr_features)) )

correlation calculation, done
progress: 0.00 %
progress: 0.11 %
progress: 0.22 %
progress: 0.33 %
progress: 0.44 %
progress: 0.55 %
progress: 0.66 %
progress: 0.77 %
progress: 0.88 %
progress: 0.99 %
progress: 1.10 %
progress: 1.22 %
progress: 1.33 %
progress: 1.44 %
progress: 1.55 %
progress: 1.66 %
progress: 1.77 %
progress: 1.88 %
progress: 1.99 %
progress: 2.10 %
progress: 2.21 %
progress: 2.32 %
progress: 2.43 %
progress: 2.54 %
progress: 2.65 %
progress: 2.76 %
progress: 2.87 %
progress: 2.98 %
progress: 3.09 %
progress: 3.20 %
progress: 3.31 %
progress: 3.43 %
progress: 3.54 %
progress: 3.65 %
progress: 3.76 %
progress: 3.87 %
progress: 3.98 %
progress: 4.09 %
progress: 4.20 %
progress: 4.31 %
progress: 4.42 %
progress: 4.53 %
progress: 4.64 %
progress: 4.75 %
progress: 4.86 %
progress: 4.97 %
progress: 5.08 %
progress: 5.19 %
progress: 5.30 %
progress: 5.41 %
progress: 5.52 %
progress: 5.64 %
progress: 5.75 %
progress: 5.86 %
progress: 5.97 %
progress: 6.08 %
progress: 6.19 %
p

In [36]:
# Set을 List로 변환
corr_features = list(corr_features)

# List를 Pickle로 저장
with open('corr_del_list_{}_{}_{}.pkl'.format(coin, target_var_3, corr_cutpoint), 'wb') as f:
    pickle.dump(corr_features, f)



In [37]:
# 저장된 Pickle 파일을 로드하는 방법
with open('corr_del_list_{}_{}_{}.pkl'.format(coin, target_var_3, corr_cutpoint), 'rb') as f:
    corr_features = pickle.load(f)

print(len(corr_features))

4447


In [20]:
# correlation 이 다른 변수와 높은 변수는 삭제한다.
X.drop(labels=corr_features, axis=1, inplace=True)

# target var 도 이제 X에서 제거한다.
X.drop(target_var, axis=1, inplace=True)

c:\Users\hhkim\AppData\Local\Programs\Python\Python37\lib\site-packages\pandas\core\frame.py:4913: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,


In [21]:
X.shape

(12924, 1226)

# Feature Selction A (This one is currently working for too long.)

## Exhaustive Feature Selection

This exhaustive feature selection algorithm is a wrapper approach for brute-force evaluation of feature subsets; the best subset is selected by optimizing a specified performance metric given an arbitrary regressor or classifier.

In [ ]:
import pandas as pd

from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import roc_auc_score, r2_score
from sklearn.model_selection import train_test_split

from mlxtend.feature_selection import ExhaustiveFeatureSelector as EFS

In [ ]:
# 이 코드는 거의 안 돌아간다고 보면 된다. RTX3080으로 10000시간 돌았는데 안 끝남.

# exhaustive search

# in order to shorter search time for the demonstration
# i will ask the algorithm to try all possible 10 and 11
# feature combinations

# if you have access to a multicore or distributed computer
# system you can try more greedy searches

efs = EFS(RandomForestRegressor(n_estimators=5,
                                n_jobs=4,
                                random_state=0,
                                max_depth=2),
          min_features=1,
          max_features=2,
          scoring='r2',
          print_progress=True,
          cv=2)

efs = efs.fit(X, y)

In [ ]:
data.columns[list(efs.best_idx_)]

# Feature Selction B (이것도 이번 논문에서는 일단 제외)

## Embedded Methods: Linear Model Coefficients

train a Linear regression model and select features with higher coefficients.

In [ ]:
# the features in the house dataset are in different scales
# so we train a scaler to scale them

scaler = StandardScaler()
scaler.fit(X)

# the LinearRegression object from sklearn is a non-regularised
# linear method. It fits by matrix multiplication and not 
# gradient descent.
# therefore we don't need to specify penalty and other parameters

sel_ = SelectFromModel(LinearRegression())

sel_.fit(scaler.transform(X), y)

# let's count the number of variables selected
selected_feat = X.columns[(sel_.get_support())]

# 저장할 파일 이름
file_name = "selected_feat_linear_coeff.pkl"

# selected_feat 변수를 pkl 파일로 저장
with open(file_name, 'wb') as file:
    pickle.dump(selected_feat, file)

print(f"{file_name} 파일이 저장되었습니다.")

print(len(selected_feat))


# and now, let's compare the  amount of selected features
# with the amount of features which coefficient is above the
# mean coefficient, to make sure we understand the output of
# sklearn

print('total features: {}'.format((X.shape[1])))

print('selected features: {}'.format(len(selected_feat)))

print(
    'features with coefficients greater than the mean coefficient: {}'.format(
        np.sum(
            np.abs(sel_.estimator_.coef_) > np.abs(
                sel_.estimator_.coef_).mean())))

In [ ]:
selected_feat

# Feature Selction C

## Embedded Methods: Tree Importance

train a Linear regression model and select features with higher coefficients.

In [38]:
from sklearn.ensemble import RandomForestRegressor

In [39]:
# RandomForestRegressor 모델 학습
model = RandomForestRegressor(n_estimators=128, random_state=42, verbose=True)
model.fit(X, y)

# 특성 중요도 출력
feature_importances = model.feature_importances_
print("Feature Importances:", feature_importances)

# 특성 선택: 중요도가 높은 순서대로 특성 선택 (임계값 설정 가능)
selected_features_indices = feature_importances.argsort()[::-1]  # 중요도 내림차순 정렬
selected_features = X.columns[selected_features_indices]
print("Selected Features:", selected_features)

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Feature Importances: [1.05194187e-09 4.78676759e-10 1.37353102e-10 ... 1.39174183e-09
 2.01148085e-09 7.65553264e-11]
Selected Features: Index(['dv5_realized_volatility_mean0',
       'realized_volatility_mean0_nn4_high_low_gap_m_p1_median',
       'tvpl_ep5_nn16_liq_last_2_m_p1_mean',
       'bidask_spread_1_nn8_tvpl2_m_p1_mean',
       'highest_return_nn16_tvpl2_m_p1_median',
       'liq_last_1_nn2_high5_nn_m_mean', 'tvpl2_nn8_return_m_p1_mean',
       'tvpl_ep1_nn16_liq_last_2_m_p1_mean',
       'tvpl_ep2_nn1_ep_liq_2_m_p1_median',
       'liq_last_1_nn8_all_nn_m_p1_median',
       ...
       'BB_width_w10_nn16_liq_last_1_m_p1_mean',
       'ep_liq_1_nn4_ep_liq_2_m_p1_median',
       'trade.tau_nn16_ep_liq_2_m_p1_median', 'ep_liq_5_nn4_low5_nn_m_mean',
       'trade.tau_nn4_BB_width_w10_m_p1_mean', 'ep_liq_5_nn16_two_m_mean',
       'tvpl5_nn16_liq_last_1_m_p1_median', 'tvpl2_nn1_liq_last_1_m_p1_median',
       'tvpl_ep2_nn2_two_m_mean', 'liq_last_2_nn4_hausdorff_mean'],
      dtype

[Parallel(n_jobs=1)]: Done 128 out of 128 | elapsed:  9.2min finished


In [40]:
# 저장할 파일 이름
file_name = "selected_feat_RF_{}_{}_{}.pkl".format(coin, target_var_3, corr_cutpoint)

# selected_feat 변수를 pkl 파일로 저장
with open(file_name, 'wb') as file:
    pickle.dump(selected_features, file)

print(f"{file_name} 파일이 저장되었습니다.")

print(len(selected_features))


# 저장할 파일 이름
file_name2 = "feature_importances_RF_{}_{}_{}.pkl".format(coin, target_var_3, corr_cutpoint)

# selected_feat 변수를 pkl 파일로 저장
with open(file_name2, 'wb') as file:
    pickle.dump(feature_importances, file)

print(f"{file_name2} 파일이 저장되었습니다.")

print(len(feature_importances))


selected_feat_RF_BTC_dv5_90.pkl 파일이 저장되었습니다.
9050
feature_importances_RF_BTC_dv5_90.pkl 파일이 저장되었습니다.
9050


In [41]:
# 저장된 Pickle 파일을 로드하는 방법

file_name = "selected_feat_RF_{}_{}_{}.pkl".format(coin, target_var_3, corr_cutpoint)

with open(file_name, 'rb') as f:
    selected_features = pickle.load(f)

print(len(selected_features))


# 저장된 Pickle 파일을 로드하는 방법
file_name2 = "feature_importances_RF_{}_{}_{}.pkl".format(coin, target_var_3, corr_cutpoint)

with open(file_name2, 'rb') as f2:
    feature_importances_ranfo = pickle.load(f2)

print(len(feature_importances_ranfo))


9050
9050


In [42]:
# 리스트를 DataFrame으로 변환
data = {'Name': list(selected_features), 'Importance': sorted(list(feature_importances), reverse=True)}
df = pd.DataFrame(data)

# DataFrame 출력
df.head(50)


Name  Importance
0                       dv5_realized_volatility_mean0    0.999357
1   realized_volatility_mean0_nn4_high_low_gap_m_p...    0.000023
2                  tvpl_ep5_nn16_liq_last_2_m_p1_mean    0.000021
3                 bidask_spread_1_nn8_tvpl2_m_p1_mean    0.000016
4               highest_return_nn16_tvpl2_m_p1_median    0.000013
5                      liq_last_1_nn2_high5_nn_m_mean    0.000013
6                          tvpl2_nn8_return_m_p1_mean    0.000012
7                  tvpl_ep1_nn16_liq_last_2_m_p1_mean    0.000012
8                   tvpl_ep2_nn1_ep_liq_2_m_p1_median    0.000012
9                   liq_last_1_nn8_all_nn_m_p1_median    0.000011
10                BB_width_w10_nn16_tvpl5_m_p1_median    0.000011
11                     tvpl2_nn4_liq_last_2_m_p1_mean    0.000011
12                  tvpl_ep5_nn1_ep_liq_2_m_p1_median    0.000010
13                ep_liq_1_nn4_high_low_gap_m_p1_mean    0.000010
14  highest_return_nn16_realized_volatility_mean0_...    0.000010
15              tvpl_ep1_nn1_highest_return_m_p1_mean    0.000009
16                       ep_liq_5_nn8_tvpl5_m_p1_mean    0.000008
17                liq_last_2_nn8_tvpl_ep2_m_p1_median    0.000007
18         dv2_lowest_return_nn8_ep_liq_1_m_p1_median    0.000007
19            ep_liq_1_nn16_lowest_return_m_p1_median    0.000007
20              ep_liq_2_nn4_high_low_gap_m_p1_median    0.000006
21                   liq_last_1_nn2_tvpl1_m_p1_median    0.000006
22                            tvpl2_nn16_two_m_median    0.000006
23                          tvpl1_nn4_tvpl2_m_p1_mean    0.000005
24                 lowest_return_nn8_hausdorff_median    0.000005
25                      liq_last_2_nn4_low5_nn_m_mean    0.000005
26   dv2_lowest_return_nn16_lowest_return_m_p1_median    0.000003
27                   trade.tau_nn16_tvpl1_m_p1_median    0.000003
28         bidask_spread_1_nn16_trade.tau_m_p1_median    0.000003
29                         tvpl1_nn8_low5_nn_m_median    0.000003
30                  liq_last_2_nn8_tvpl_ep2_m_p1_mean    0.000003
31      BB_width_w20_nn16_bidask_spread_0_m_p1_median    0.000003
32          bidask_spread_0_nn16_liq_last_2_m_p1_mean    0.000003
33          bidask_spread_1_nn1_high5_abs_nn_m_median    0.000003
34         BB_width_w20_nn8_lowest_return_m_p1_median    0.000003
35                lowest_return_nn16_hausdorff_median    0.000002
36                 liq_last_2_nn4_trade.tau_m_p1_mean    0.000002
37  realized_volatility_mean0_nn8_tvpl_ep1_m_p1_me...    0.000002
38               trade_vol_nn8_BB_width_w40_m_p1_mean    0.000002
39           bidask_spread_0_nn16_trade_vol_m_p1_mean    0.000002
40           tvpl_ep2_nn1_bidask_spread_0_m_p1_median    0.000002
41               trade_vol_nn1_BB_width_w40_m_p1_mean    0.000002
42       bidask_spread_1_nn1_highest_return_m_p1_mean    0.000002
43               BB_width_w40_nn1_high5_abs_nn_m_mean    0.000002
44                return_nn2_BB_width_w20_m_p1_median    0.000002
45              BB_width_w40_nn8_ep_liq_1_m_p1_median    0.000002
46    dv2_lowest_return_nn2_bidask_spread_0_m_p1_mean    0.000002
47          BB_width_w20_nn2_BB_width_w40_m_p1_median    0.000002
48                    trade_vol_nn8_tvpl5_m_p1_median    0.000002
49                     liq_last_1_nn4_tvpl5_m_p1_mean    0.000002

In [43]:
df.to_csv('D:/OneDrive - 한동대학교/PROJECT/트머프로젝트/output/temp_RF_important_features.csv')